In [6]:
import pandas as pd
import json

In [2]:
with open('../data/data_salto/concursos/concursos_salto_nacional_2025.json', 'r', encoding='utf-8') as file:
    datos_concursos = json.load(file)

df_concursos = pd.DataFrame(datos_concursos)
df_concursos = df_concursos.rename(columns = {"Nombre": "Concurso", "Categoría": "Categoria_concurso"})
df_concursos["Concurso"] = df_concursos["Concurso"].str.strip()
df_concursos.head()

Concurso Categoria_concurso  \
0                                     CSN3* Invierno             CSN***   
1                              SPRING MET I 2025 YH*            CSI YH*   
2                      SPRING MET I 2025 - SILVER 1*               CSI*   
3                        SPRING MET I 2025 - GOLD 2*              CSI**   
4  CSIYH* - 1st Week Andalucía Pre-Sunshine Tour ...            CSI YH*   

  Provincia                   Localidad           Disciplina  \
0   Sevilla            Real Club Pineda  Salto de Obstáculos   
1  Valencia  Centro Ecuestre Oliva Nova  Salto de Obstáculos   
2  Valencia  Centro Ecuestre Oliva Nova  Salto de Obstáculos   
3  Valencia  Centro Ecuestre Oliva Nova  Salto de Obstáculos   
4     Cádiz          Dehesa Montenmedio  Salto de Obstáculos   

                               Federación Resultados   País      Inicio  \
0              Federación Hípica Andaluza        Ver  Epaña  10/01/2025   
1  Federación Hípica Comunidad Valenciana        Ver  Epaña  14/01/2025   
2  Federación Hípica Comunidad Valenciana        Ver  Epaña  16/01/2025   
3  Federación Hípica Comunidad Valenciana        Ver  Epaña  16/01/2025   
4              Federación Hípica Andaluza        Ver  Epaña  16/01/2025   

        Final         Ambito  
0  12/01/2025       Nacional  
1  16/01/2025  Internacional  
2  18/01/2025  Internacional  
3  19/01/2025  Internacional  
4  19/01/2025  Internacional

In [3]:
df_pruebas_resultados = pd.read_csv("../data/data_salto/resultados_combinados_2025.csv", index_col=0)
df_pruebas_resultados.head()

C:\Users\gabri\AppData\Local\Temp\ipykernel_13084\1077302799.py:1: DtypeWarning: Columns (3,6) have mixed types. Specify dtype option on import or set low_memory=False.
  df_pruebas_resultados = pd.read_csv("../data/data_salto/resultados_combinados_2025.csv", index_col=0)


Estado Posicion Lic_jinete                       Jinete Pais_jinete  \
0    FIN        1     284725  Pedro Miguel DA SILVA MANSO         ESP   
1    FIN        2      77612        Ignacio ASTOLFI LÓPEZ         ESP   
2    FIN        3     306183     Francisco PICAO CALDEIRA         ESP   
3    FIN        4       1004          Jesús TORRES GARCÍA         ESP   
4    FIN        5     367363              Nina FAGERSTROM         ESP   

  Lic_caballo              Caballo Raza_caballo Pais_caballo Puntuacion  ...  \
0      169882  BRIDGETOWN JONES OS      (Indt.)          ESP    0/59,91  ...   
1      157373       QUINTO BLUE PS        OLDBG          ESP    0/63,23  ...   
2      145996         FLOR DU PASO        CRPOR          ESP    0/65,58  ...   
3      170075          DIABETTO PS        OLDBG          ESP    0/66,00  ...   
4      170155    HASENACHER CERVIN         ZANG          ESP    0/66,78  ...   

   Categoria  Ptos_obs_R1 Ptos_tiempo_R1 Tiempo_R1 Ptos_obs_R2 Ptos_tiempo_R2  \
0     CSN***          0.0            NaN     59.91         NaN            NaN   
1     CSN***          0.0            NaN     63.23         NaN            NaN   
2     CSN***          0.0            NaN     65.58         NaN            NaN   
3     CSN***          0.0            NaN     66.00         NaN            NaN   
4     CSN***          0.0            NaN     66.78         NaN            NaN   

   Tiempo_R2  Ptos_obs_R3  Ptos_tiempo_R3  Tiempo_R3  
0        NaN          NaN             NaN        NaN  
1        NaN          NaN             NaN        NaN  
2        NaN          NaN             NaN        NaN  
3        NaN          NaN             NaN        NaN  
4        NaN          NaN             NaN        NaN  

[5 rows x 25 columns]

In [ ]:
& (df_final["Categoria"] == df_final["Categoria_concurso"])

In [15]:
df_final = pd.merge(df_pruebas_resultados, df_concursos, on = "Concurso", how = "inner")
df_final['Fecha_prueba'] = pd.to_datetime(df_final['Fecha_prueba'])
df_final['Inicio'] = pd.to_datetime(df_final['Inicio'], dayfirst=True)
df_final['Final'] = pd.to_datetime(df_final['Final'], dayfirst=True)
df_final = df_final[(df_final['Fecha_prueba'] >= df_final['Inicio']) & (df_final['Fecha_prueba'] <= df_final['Final'])]
df_final = df_final.drop(['Puntuacion', 'Resultados', 'Categoria_concurso', 'Pais_jinete', 'Pais_caballo', 'Raza_caballo'], axis=1)
df_final["Jinete"] = df_final["Jinete"].str.lower()
df_final["Caballo"] = df_final["Caballo"].str.lower()
df_final["Lic_jinete"] = df_final["Lic_jinete"].astype(str)
df_final["Lic_caballo"] = df_final["Lic_caballo"].astype(str)
# df_final["Raza_caballo"] = df_final["Raza_caballo"].apply(lambda x: None if x == '(Indt.)' else x)
df_final["Lic_jinete"] = df_final["Lic_jinete"].apply(lambda x: "10186822" if x == '--' else x)
df_final["Jinete"] = df_final["Jinete"].apply(lambda x: "jesus folch redondo" if x == '-- -- --' else x)
lista = ["ELI", "RET", "NOP"]
df_final["Posicion"] = df_final["Posicion"].apply(lambda x: None if x in lista else x)
df_final["Lic_caballo"] = df_final["Lic_caballo"].apply(lambda x: None if x == '--' else x)

lic_mas_larga_por_jinete = (
    df_final[["Jinete", "Lic_jinete"]]
    .drop_duplicates()
    .assign(longitud=lambda x: x["Lic_jinete"].astype(str).str.len())
    .sort_values("longitud", ascending=False)
    .drop_duplicates(subset="Jinete")
    .drop(columns="longitud")
    .set_index("Jinete")
)

lic_mas_larga_por_caballo = (
    df_final[["Caballo", "Lic_caballo"]]
    .drop_duplicates()
    .assign(longitud=lambda x: x["Lic_caballo"].astype(str).str.len())
    .sort_values("longitud", ascending=False)
    .drop_duplicates(subset="Caballo")
    .drop(columns="longitud")
    .set_index("Caballo")
)

# 2. Reemplazar en el DataFrame original
df_final["Lic_jinete"] = df_final["Jinete"].map(lic_mas_larga_por_jinete["Lic_jinete"])
df_final["Lic_caballo"] = df_final["Caballo"].map(lic_mas_larga_por_caballo["Lic_caballo"])
df_final


Estado Posicion Lic_jinete                          Jinete Lic_caballo  \
0         FIN        1     284725     pedro miguel da silva manso      169882   
1         FIN        2      77612           ignacio astolfi lópez      157373   
2         FIN        3     306183        francisco picao caldeira      145996   
3         FIN        4   10006303             jesús torres garcía     107ZP87   
4         FIN        5   10002400                 nina fagerstrom     105ZA09   
...       ...      ...        ...                             ...         ...   
194685    FIN       23      77612           ignacio astolfi lópez      158640   
194686    FIN       24      37013           alejandro alonso buzo      159094   
194687    RET     None   10047790  patricio de valdenebro del rey     106IJ31   
194688    NOP     None     196126      francisco román cantillana      155590   
194689    NOP     None     196126      francisco román cantillana      163007   

                        Caballo  Premio  Dinero_premio  \
0           bridgetown jones os    True          450.0   
1                quinto blue ps    True          300.0   
2                  flor du paso    True          200.0   
3                   diabetto ps    True          150.0   
4             hasenacher cervin    True          125.0   
...                         ...     ...            ...   
194685        grupo prom jivaro    True            0.0   
194686          houston du gast    True            0.0   
194687  klimax van het lindehof    True            0.0   
194688         uloubet de vanau    True            0.0   
194689         garou de blondel    True            0.0   

                                                Prueba Fecha_prueba  \
0                              1,30 - A c.c. (238.2.1)   2025-01-10   
1                              1,30 - A c.c. (238.2.1)   2025-01-10   
2                              1,30 - A c.c. (238.2.1)   2025-01-10   
3                              1,30 - A c.c. (238.2.1)   2025-01-10   
4                              1,30 - A c.c. (238.2.1)   2025-01-10   
...                                                ...          ...   
194685  1,35 - Dos fases Especial (Art. 274.2) (274.2)   2025-01-10   
194686  1,35 - Dos fases Especial (Art. 274.2) (274.2)   2025-01-10   
194687  1,35 - Dos fases Especial (Art. 274.2) (274.2)   2025-01-10   
194688  1,35 - Dos fases Especial (Art. 274.2) (274.2)   2025-01-10   
194689  1,35 - Dos fases Especial (Art. 274.2) (274.2)   2025-01-10   

              Concurso Categoria  Ptos_obs_R1  Ptos_tiempo_R1  Tiempo_R1  \
0       CSN3* Invierno    CSN***          0.0             NaN      59.91   
1       CSN3* Invierno    CSN***          0.0             NaN      63.23   
2       CSN3* Invierno    CSN***          0.0             NaN      65.58   
3       CSN3* Invierno    CSN***          0.0             NaN      66.00   
4       CSN3* Invierno    CSN***          0.0             NaN      66.78   
...                ...       ...          ...             ...        ...   
194685  CSN3* Invierno    CSN***          0.0             NaN        NaN   
194686  CSN3* Invierno    CSN***          8.0            17.0        NaN   
194687  CSN3* Invierno    CSN***          NaN             NaN        NaN   
194688  CSN3* Invierno    CSN***          NaN             NaN        NaN   
194689  CSN3* Invierno    CSN***          NaN             NaN        NaN   

        Ptos_obs_R2  Ptos_tiempo_R2  Tiempo_R2  Ptos_obs_R3  Ptos_tiempo_R3  \
0               NaN             NaN        NaN          NaN             NaN   
1               NaN             NaN        NaN          NaN             NaN   
2               NaN             NaN        NaN          NaN             NaN   
3               NaN             NaN        NaN          NaN             NaN   
4               NaN             NaN        NaN          NaN             NaN   
...             ...             ...        ...          ...             ...   
194685         12.

In [5]:
df_final.to_csv("../data/data_salto/informacion_concursos_final.csv")

NameError: name 'df_final' is not defined

In [14]:
df = pd.read_csv("../data/data_salto/informacion_concursos_final.csv", index_col = 0)
df["Disciplina"] = "Salto de Obstaculos"
i = 0
df["id_resultado"] = range(i +1 , i + 1 + len(df))
print(df["Lic_caballo"].duplicated().sum())
print(df["Caballo"].duplicated().sum())

64399
64399


C:\Users\gabri\AppData\Local\Temp\ipykernel_9364\2217570652.py:1: DtypeWarning: Columns (2) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv("../data/data_salto/informacion_concursos_final.csv", index_col = 0)


In [15]:
df.columns

Index(['Estado', 'Posicion', 'Lic_jinete', 'Jinete', 'Lic_caballo', 'Caballo',
       'Premio', 'Dinero_premio', 'Prueba', 'Fecha_prueba', 'Concurso',
       'Categoria', 'Ptos_obs_R1', 'Ptos_tiempo_R1', 'Tiempo_R1',
       'Ptos_obs_R2', 'Ptos_tiempo_R2', 'Tiempo_R2', 'Ptos_obs_R3',
       'Ptos_tiempo_R3', 'Tiempo_R3', 'Provincia', 'Localidad', 'Disciplina',
       'Federación', 'País', 'Inicio', 'Final', 'Ambito', 'id_resultado'],
      dtype='object')

In [29]:
concursos_totales = []
concursos_malos = []
for _, elemento in df.iterrows():
    if elemento["Inicio"] <= elemento["Fecha_prueba"] <= elemento["Final"]:
        concursos_totales.append(elemento[10])
        print("ok")
    else:
        concursos_malos.append(elemento[10])
        print(elemento[10])

C:\Users\gabri\AppData\Local\Temp\ipykernel_15708\2862145148.py:5: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  concursos_totales.append(elemento[10])


ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
o

In [31]:
concursos_totales = list(set(concursos_totales))
len(concursos_totales)

75

In [3]:
pd.set_option('display.max_columns', None)

In [4]:
df[df["Concurso"] == "MOURATOURS"]

Estado Posicion  Lic_jinete                          Jinete  \
188620    FIN      1.0        2659          katia bosque izquierdo   
188621    FIN      2.0       46311              miguel laiz zandio   
188622    FIN      3.0       33550         santiago escrig sánchez   
188623    FIN      4.0    10366476            natalia bernal lluch   
188624    FIN      5.0    10083655          carmen casan serneguet   
...       ...      ...         ...                             ...   
188762    FIN     18.0       60682        carmen hernández yanguas   
188763    FIN     19.0      243809        sophie schwarck asmussen   
188764    FIN     20.0    10338242              mickael weislinger   
188765    FIN     21.0    10056467  guillermo diez-delgado guitian   
188766    FIN     22.0    10075188                      remy ellis   

       Lic_caballo                     Caballo  Premio  Dinero_premio  \
188620      168410            j'aime cassendra    True           49.0   
188621      166951               poker face lz    True           35.0   
188622      163741                    caretino    True           21.0   
188623     109BN94         kalachnikov gabkcal    True           21.0   
188624      170798                     inca bk    True           14.0   
...            ...                         ...     ...            ...   
188762      150981                      navaro    True            0.0   
188763      169998                  devil mv z    True            0.0   
188764     108PL89  dino f van de wolfsakker z    True            0.0   
188765     108CV73                   cunegundo    True            0.0   
188766     108DS15                     jay-z z    True            0.0   

                                            Prueba Fecha_prueba    Concurso  \
188620  5 años - 1,10 - Dos Fases Especial (274.2)   2025-04-18  MOURATOURS   
188621  5 años - 1,10 - Dos Fases Especial (274.2)   2025-04-18  MOURATOURS   
188622  5 años - 1,10 - Dos Fases Especial (274.2)   2025-04-18  MOURATOURS   
188623  5 años - 1,10 - Dos Fases Especial (274.2)   2025-04-18  MOURATOURS   
188624  5 años - 1,10 - Dos Fases Especial (274.2)   2025-04-18  MOURATOURS   
...                                            ...          ...         ...   
188762  7 años - 1,30 - Dos Fases Especial (274.2)   2025-04-20  MOURATOURS   
188763  7 años - 1,30 - Dos Fases Especial (274.2)   2025-04-20  MOURATOURS   
188764  7 años - 1,30 - Dos Fases Especial (274.2)   2025-04-20  MOURATOURS   
188765  7 años - 1,30 - Dos Fases Especial (274.2)   2025-04-20  MOURATOURS   
188766  7 años - 1,30 - Dos Fases Especial (274.2)   2025-04-20  MOURATOURS   

       Categoria  Ptos_obs_R1  Ptos_tiempo_R1  Tiempo_R1  Ptos_obs_R2  \
188620     CSNCJ          NaN             0.0        NaN          0.0   
188621     CSNCJ          NaN             0.0        NaN          0.0   
188622     CSNCJ          0.0             NaN        NaN          4.0   
188623     CSNCJ          0.0             NaN        NaN          4.0   
188624     CSNCJ          NaN             4.0        NaN          0.0   
...          ...          ...             ...        ...          ...   
188762     CSNCJ          4.0             0.0        NaN          4.0   
188763     CSNCJ          4.0             0.0        NaN          4.0   
188764     CSNCJ          4.0             0.0        NaN          4.0   
188765     CSNCJ          8.0             0.0        NaN          8.0   
188766     CSNCJ          8.0            16.0        NaN          8.0   

        Ptos_tiempo_R2  Tiempo_R2  Ptos_obs_R3  Ptos_tiempo_R3  Tiempo_R3  \
188620             NaN      44.12          NaN             NaN        NaN   
188621             NaN      52.93          NaN             NaN        NaN   
188622             0.0      44.15          NaN             NaN        NaN   
188623             0.0      44.81          NaN             NaN        NaN   
188624             NaN      45.86          NaN             NaN        NaN   
.

In [8]:
df_coso = df[["Concurso", "Prueba"]]
concurso_pruebas = {}
concurso_pruebas = {}
for _, row in df_coso.iterrows():  # Usar el dataframe df que proporcionaste
    concurso = row["Concurso"]
    prueba = row["Prueba"]
    if concurso in concurso_pruebas:
        if prueba not in concurso_pruebas[concurso]: # Añadido esta condición
            concurso_pruebas[concurso].append(prueba)
    else:
        concurso_pruebas[concurso] = [prueba]

concurso_pruebas

{'CSN3* Invierno': ['1,30 - A c.c. (238.2.1)',
  '1,20 - A c.c. (238.2.1)',
  '1,25 - Dos Fases Especial (274.2)',
  '1,40 - A c.c. (238.2.1)',
  '1.35 GP - Acc y desempate (238.2.2)',
  '1,30 - Dos fases Especial (Art. 274.2) (274.2)',
  '1,40 gp - A.c.c. y desempate al cronómetro (238.2.2)',
  '1,35 - Dos fases Especial (Art. 274.2) (274.2)'],
 'SPRING MET I 2025 YH*': ['6 años - 1,25 - A sin cronómetro (238.1.1)',
  '7 años - 1,35 - A sin cronómetro (238.1.1)',
  '5 años - 1,15 - A.c.c. y desempate (238.2.2)',
  '6 años - 1,25 - A.c.c. y desempate (238.2.2)',
  '7 años - 1,35 - A.c.c. y desempate (238.2.2)',
  '5 años - 1,15 - Dos Fases Especial (274.2)',
  '6 años - 1,25 - Dos Fases Especial (274.2)',
  '7 años - 1,35 - Dos Fases Especial (274.2)',
  '5 años - 1,15 - A sin cronómetro (238.1.1)'],
 'MOURA TOURS VALENCIA - SPRING TOUR': ['1,35 (G) - A c.c. (238.2.1)',
  '1,30 - A c.c. (238.2.1)',
  '1,40 (G) - DOS FASES (A c/c - A c/c) (274.1.5.3)',
  '1,45 (G) - A c.c. (238.2.1)',
 

## Inserción a BBDD

In [1]:
import psycopg2 as ps

In [4]:
import pandas as pd
from sqlalchemy import create_engine, text

# CONFIGURA TU CONEXIÓN
usuario = 'postgres'
password = 'admin'
host = 'localhost'
puerto = 5432
basedatos = 'BBDD_Hipica'

# CREA EL MOTOR DE CONEXIÓN
engine = create_engine(f'postgresql+psycopg2://{usuario}:{password}@{host}:{puerto}/{basedatos}')

In [2]:
conn = ps.connect(
    dbname = "BBDD_Hipica", # base a la que nos queremos conectar
    user = "postgres",
    password = "admin",
    host = "localhost",
    port = "5432" # puerto en el que s eencuentra postgres
)

In [3]:
cur = conn.cursor()

In [4]:
# COmprobamos que la conexión está creada y conectada
cur.execute("SELECT version();")
cur.fetchone() 

('PostgreSQL 16.4, compiled by Visual C++ build 1940, 64-bit',)

### Inserción disciplinas

In [7]:
data_insert_disciplinas = ["Salto de Obstaculos", "Concurso Completo", "Doma clasica"]


In [8]:
data_to_insert = [(disciplina,) for disciplina in data_insert_disciplinas]

In [9]:
# Creamos la query de inserción de los datos de ciudad
insert_query_disciplinas = """ 
                        INSERT INTO disciplinas(disciplina)
                        VALUES (%s) 
"""

In [19]:
conn.rollback()

In [12]:
query2 = """
    SELECT * 
    FROM disciplinas; 
"""
cur.execute(query2)
cur.fetchall()

[(1, 'Salto de Obstaculos'), (2, 'Concurso Completo'), (3, 'Doma clasica')]

In [11]:
# Ejecutamos la query para insertar las disciplinas
cur.executemany(insert_query_disciplinas, data_to_insert)
conn.commit()

### Inserción caballos

In [13]:
df_caballos = df[["Lic_caballo", "Caballo"]]

In [14]:
# Creamos la lista que va a contener toda la información 
data_insert_caballos = []

# Vamos iterando por cada columna del dataframe y cada fila de cada columna, obteniendo los elementos de las filas (row)
for i, row in df_caballos.iterrows():
    id_caballo = row["Lic_caballo"]
    nombre_caballo = row["Caballo"]

    tupla_caballo = (id_caballo, nombre_caballo)

    if tupla_caballo not in data_insert_caballos:
        data_insert_caballos.append(tupla_caballo)

In [15]:
insert_query_caballos = """ 
                        INSERT INTO caballos (id_caballo, nombre_caballo)
                        VALUES (%s, %s)
"""    

In [16]:
# Ejecutamos la query y le indicamos los valores 
cur.executemany(insert_query_caballos, data_insert_caballos)
conn.commit()  

### Inserción jinetes

In [17]:
df_jinetes = df[["Lic_jinete", "Jinete"]]

In [18]:
# Creamos la lista que va a contener toda la información 
data_insert_jinetes = []

# Vamos iterando por cada columna del dataframe y cada fila de cada columna, obteniendo los elementos de las filas (row)
for i, row in df_jinetes.iterrows():
    id_jinete = row["Lic_jinete"]
    nombre_jinete = row["Jinete"]

    tupla_jinete = (id_jinete, nombre_jinete)

    if tupla_jinete not in data_insert_jinetes:
        data_insert_jinetes.append(tupla_jinete)

In [19]:
insert_query_jinetes = """ 
                        INSERT INTO jinetes (id_jinete, nombre_jinete)
                        VALUES (%s, %s)
"""

In [20]:
# Ejecutamos la query y le indicamos los valores 
cur.executemany(insert_query_jinetes, data_insert_jinetes)
conn.commit()

### Inserción concursos

In [21]:
df_concursos = df[["Concurso", "Categoria", "País", "Provincia", "Localidad", "Ambito", "Federación", "Inicio", "Final"]]

In [22]:
# Creamos la lista que va a contener toda la información 
data_insert_concursos = []
# Vamos iterando por cada columna del dataframe y cada fila de cada columna, obteniendo los elementos de las filas (row)
for i, row in df_concursos.iterrows():
    nombre_concurso = row["Concurso"]
    categoria_concurso = row["Categoria"]
    pais_concurso = row["País"]
    provincia_concurso = row["Provincia"]
    localidad_concurso = row["Localidad"]
    ambito_concurso = row["Ambito"]
    federacion_concurso = row["Federación"]
    inicio_concurso = row["Inicio"]
    final_concurso = row["Final"]

    tupla_concursos = (nombre_concurso, categoria_concurso, pais_concurso, provincia_concurso, 
                       localidad_concurso, ambito_concurso, federacion_concurso, 
                       inicio_concurso, final_concurso)

    if tupla_concursos not in data_insert_concursos:
        data_insert_concursos.append(tupla_concursos)

In [23]:
insert_query_concursos = """ 
                        INSERT INTO concursos (nombre_concurso, categoria_concurso, 
                                               pais_concurso, provincia_concurso, 
                                               localidad_concurso, ambito_concurso,
                                               federacion_concurso, fecha_inicio_concurso,
                                               fecha_fin_concurso)
                        VALUES (%s, %s,  %s, %s, %s, %s, %s, %s, %s)
"""

In [24]:
# Ejecutamos la query y le indicamos los valores 
cur.executemany(insert_query_concursos, data_insert_concursos)
conn.commit()


### Inserción pruebas

In [25]:
cur.execute("SELECT disciplina, id_disciplina FROM disciplinas")
dictio_disciplinas = dict(cur.fetchall())

In [26]:
df_pruebas = df[["Prueba", "Fecha_prueba", "Disciplina"]]

In [27]:
data_insert_pruebas = []

for _, row in df_pruebas.iterrows():
    nombre_prueba = row["Prueba"]
    fecha_prueba = row["Fecha_prueba"]
    disciplina_prueba = dictio_disciplinas.get(row["Disciplina"])

    tupla_pruebas = (nombre_prueba, fecha_prueba, disciplina_prueba)

    if tupla_pruebas not in data_insert_pruebas:
        data_insert_pruebas.append(tupla_pruebas)

In [28]:
insert_query_pruebas = """ 
                        INSERT INTO pruebas (nombre_prueba, fecha_prueba,id_disciplina)
                        VALUES (%s, %s,  %s)
"""

In [29]:
# Ejecutamos la query y le indicamos los valores 
cur.executemany(insert_query_pruebas, data_insert_pruebas)
conn.commit()

### Inserción resultados

In [19]:
cur.execute("SELECT nombre_jinete, id_jinete FROM jinetes")
dictio_jinetes = dict(cur.fetchall())
cur.execute("SELECT nombre_caballo, id_caballo FROM caballos")
dictio_caballos = dict(cur.fetchall())
cur.execute("SELECT nombre_concurso, id_concurso FROM concursos")
dictio_concursos = dict(cur.fetchall())
cur.execute("SELECT id_prueba, nombre_prueba, fecha_prueba FROM pruebas")
coso = cur.fetchall()
df_pruebas = pd.DataFrame(coso)
df_pruebas = df_pruebas.rename(columns = {0 : "id_prueba", 1 : "Prueba", 2: "Fecha_prueba"})
df_pruebas['Fecha_prueba'] = pd.to_datetime(df_pruebas['Fecha_prueba'])


In [20]:
df_pruebas

id_prueba                                             Prueba  \
0             1                            1,30 - A c.c. (238.2.1)   
1             2         6 años - 1,25 - A sin cronómetro (238.1.1)   
2             3                        1,35 (G) - A c.c. (238.2.1)   
3             4         7 años - 1,35 - A sin cronómetro (238.1.1)   
4             5       5 años - 1,15 - A.c.c. y desempate (238.2.2)   
...         ...                                                ...   
1136       1137                            1,40 - A c.c. (238.2.1)   
1137       1138                1.35 GP - Acc y desempate (238.2.2)   
1138       1139     1,30 - Dos fases Especial (Art. 274.2) (274.2)   
1139       1140  1,40 gp - A.c.c. y desempate al cronómetro (23...   
1140       1141     1,35 - Dos fases Especial (Art. 274.2) (274.2)   

     Fecha_prueba  
0      2025-01-10  
1      2025-01-14  
2      2025-01-24  
3      2025-01-14  
4      2025-01-15  
...           ...  
1136   2025-04-26  
1137   2025-04-26  
1138   2025-04-27  
1139   2025-04-27  
1140   2025-01-10  

[1141 rows x 3 columns]

In [21]:
df_resultados = df[["id_resultado", "Jinete", "Caballo", "Concurso", "Prueba", "Posicion", "Estado", "Premio", "Dinero_premio", "Fecha_prueba", "Inicio", "Final"]]
df_resultados['Fecha_prueba'] = pd.to_datetime(df_resultados['Fecha_prueba'])
df_resultados['Inicio'] = pd.to_datetime(df_resultados['Inicio'])
df_resultados['Final'] = pd.to_datetime(df_resultados['Final'])

C:\Users\gabri\AppData\Local\Temp\ipykernel_9364\3065513238.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_resultados['Fecha_prueba'] = pd.to_datetime(df_resultados['Fecha_prueba'])
C:\Users\gabri\AppData\Local\Temp\ipykernel_9364\3065513238.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_resultados['Inicio'] = pd.to_datetime(df_resultados['Inicio'])
C:\Users\gabri\AppData\Local\Temp\ipykernel_9364\3065513238.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from

In [22]:
df_resultados

id_resultado                          Jinete                  Caballo  \
0                  1     pedro miguel da silva manso      bridgetown jones os   
1                  2           ignacio astolfi lópez           quinto blue ps   
2                  3        francisco picao caldeira             flor du paso   
3                  4             jesús torres garcía              diabetto ps   
4                  5                 nina fagerstrom        hasenacher cervin   
...              ...                             ...                      ...   
194685         72728           ignacio astolfi lópez        grupo prom jivaro   
194686         72729           alejandro alonso buzo          houston du gast   
194687         72730  patricio de valdenebro del rey  klimax van het lindehof   
194688         72731      francisco román cantillana         uloubet de vanau   
194689         72732      francisco román cantillana         garou de blondel   

              Concurso                                          Prueba  \
0       CSN3* Invierno                         1,30 - A c.c. (238.2.1)   
1       CSN3* Invierno                         1,30 - A c.c. (238.2.1)   
2       CSN3* Invierno                         1,30 - A c.c. (238.2.1)   
3       CSN3* Invierno                         1,30 - A c.c. (238.2.1)   
4       CSN3* Invierno                         1,30 - A c.c. (238.2.1)   
...                ...                                             ...   
194685  CSN3* Invierno  1,35 - Dos fases Especial (Art. 274.2) (274.2)   
194686  CSN3* Invierno  1,35 - Dos fases Especial (Art. 274.2) (274.2)   
194687  CSN3* Invierno  1,35 - Dos fases Especial (Art. 274.2) (274.2)   
194688  CSN3* Invierno  1,35 - Dos fases Especial (Art. 274.2) (274.2)   
194689  CSN3* Invierno  1,35 - Dos fases Especial (Art. 274.2) (274.2)   

       Posicion Estado  Premio  Dinero_premio Fecha_prueba     Inicio  \
0             1    FIN    True          450.0   2025-01-10 2025-01-10   
1             2    FIN    True          300.0   2025-01-10 2025-01-10   
2             3    FIN    True          200.0   2025-01-10 2025-01-10   
3             4    FIN    True          150.0   2025-01-10 2025-01-10   
4             5    FIN    True          125.0   2025-01-10 2025-01-10   
...         ...    ...     ...            ...          ...        ...   
194685     23.0    FIN    True            0.0   2025-01-10 2025-01-10   
194686     24.0    FIN    True            0.0   2025-01-10 2025-01-10   
194687      NaN    RET    True            0.0   2025-01-10 2025-01-10   
194688      NaN    NOP    True            0.0   2025-01-10 2025-01-10   
194689      NaN    NOP    True            0.0   2025-01-10 2025-01-10   

            Final  
0      2025-01-12  
1      2025-01-12  
2      2025-01-12  
3      2025-01-12  
4      2025-01-12  
...           ...  
194685 2025-01-12  
194686 2025-01-12  
194687 2025-01-12  
194688 2025-01-12  
194689 2025-01-12  

[72732 rows x 12 columns]

In [40]:
# Unir por nombre de prueba y fecha exacta

df_merged = pd.merge(df_resultados, df_pruebas, left_on=['Prueba', 'Fecha_prueba'], right_on=['Prueba', 'Fecha_prueba'], how='left')
df_resultados_bueno = df_merged.drop(columns = ["Prueba", "Fecha_prueba", "Inicio", "Final"], axis = 1)

In [33]:
df_merged[df_merged["Concurso"] == 'MOURATOURS']["Prueba"].unique()

array(['5 años - 1,10 - Dos Fases Especial (274.2)',
       '6 años - 1,20 - Dos Fases Especial (274.2)',
       '7 años - 1,30 - Dos Fases Especial (274.2)',
       '5 años - 1,10 - A c.c. (238.2.1)',
       '6 años - 1,20 - A c.c. (238.2.1)',
       '7 años - 1,30 - A c.c. (238.2.1)'], dtype=object)

In [38]:
concursos_totales = []
concursos_malos = []
for _, elemento in df_merged.iterrows():
    if elemento["Inicio"] <= elemento["Fecha_prueba"] <= elemento["Final"]:
        concursos_totales.append(elemento[10])
        print("ok")
    else:
        concursos_malos.append(elemento[10])
        print(elemento[10])

C:\Users\gabri\AppData\Local\Temp\ipykernel_15708\2240790449.py:5: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  concursos_totales.append(elemento[10])


ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
o

In [39]:
concursos_malos

[]

In [ ]:
data_insert_resultados = []
lista = ["ELI", "NOP", "RET", "DSQ", "ret", "nop", "dsq", "eli"]

for _, row in df_resultados_bueno.iterrows():
    
    id_resultado = int(row["id_resultado"])
    id_jinete = dictio_jinetes.get(row["Jinete"])
    id_caballo = dictio_caballos.get(row["Caballo"])
    id_concurso = dictio_concursos.get(row["Concurso"]) # coger fecha inicio del concurso?
    id_prueba = row["id_prueba"]
    # puesto debe ser None si es NaN o está en lista
    puesto = row["Posicion"] if pd.notna(row["Posicion"]) and row["Posicion"] not in lista else None
    estado = row["Estado"]
    premio = row["Premio"]
    dinero_premio = row["Dinero_premio"]

    tupla_resultados = (id_resultado, id_jinete, id_caballo, id_prueba, id_concurso, puesto, estado, premio, dinero_premio)

    if tupla_resultados not in data_insert_resultados:
        data_insert_resultados.append(tupla_resultados)

In [35]:
len(data_insert_resultados)

72732

In [36]:
insert_query_resultados = """ 
                        INSERT INTO resultados (id_resultado, id_jinete, id_caballo, id_prueba, id_concurso, puesto, estado, premio, dinero_premio)
                        VALUES (%s, %s, %s,  %s, %s, %s, %s, %s, %s)
"""

In [37]:
# Ejecutamos la query y le indicamos los valores 

cur.executemany(insert_query_resultados, data_insert_resultados)
conn.commit()

### Inserción resultados salto

In [38]:
df_resultados_salto = df[["Disciplina","id_resultado", "Ptos_obs_R1", "Ptos_tiempo_R1", "Tiempo_R1", "Ptos_obs_R2", "Ptos_tiempo_R2", "Tiempo_R2", "Ptos_obs_R3", "Ptos_tiempo_R3", "Tiempo_R3"]]

In [39]:
cur.execute("SELECT id_resultado FROM resultados")
resultados_existentes = {row[0]: None for row in cur.fetchall()}

In [40]:
data_insert_resultados_salto = []


for _, row in df_resultados_salto.iterrows():
    id_resultado = row["id_resultado"]
    if id_resultado not in resultados_existentes:
        print(f"Error: El id_resultado {id_resultado} del dataframe no existe en la tabla resultados")
        continue 

    id_disciplina = dictio_disciplinas.get(row["Disciplina"])

    ptos_obs_r1 = row["Ptos_obs_R1"] if pd.notna(row["Ptos_obs_R1"]) else None
    ptos_tmp_r1 = row["Ptos_tiempo_R1"] if pd.notna(row["Ptos_tiempo_R1"]) else None
    tiempo_r1 = row["Tiempo_R1"] if pd.notna(row["Tiempo_R1"]) else None

    ptos_obs_r2 = row["Ptos_obs_R2"] if pd.notna(row["Ptos_obs_R2"]) else None
    ptos_tmp_r2 = row["Ptos_tiempo_R2"] if pd.notna(row["Ptos_tiempo_R2"]) else None
    tiempo_r2 = row["Tiempo_R2"] if pd.notna(row["Tiempo_R2"]) else None

    ptos_obs_r3 = row["Ptos_obs_R3"] if pd.notna(row["Ptos_obs_R3"]) else None
    ptos_tmp_r3 = row["Ptos_tiempo_R3"] if pd.notna(row["Ptos_tiempo_R3"]) else None
    tiempo_r3 = row["Tiempo_R3"] if pd.notna(row["Tiempo_R3"]) else None


    tupla_resultados_salto = (id_resultado, id_disciplina, ptos_obs_r1, ptos_tmp_r1, tiempo_r1, ptos_obs_r2, ptos_tmp_r2, tiempo_r2, ptos_obs_r3, ptos_tmp_r3, tiempo_r3)

    if tupla_resultados_salto not in data_insert_resultados_salto:
        data_insert_resultados_salto.append(tupla_resultados_salto)

In [41]:

insert_query_resultados_salto = """ 
                        INSERT INTO resultados_salto (id_resultado, id_disciplina, puntos_obs_r1, puntos_tmp_r1, tiempo_r1, puntos_obs_r2, puntos_tmp_r2, tiempo_r2, puntos_obs_r3, puntos_tmp_r3, tiempo_r3)
                        VALUES (%s, %s, %s,  %s, %s, %s, %s, %s, %s, %s, %s)
"""

In [42]:


cur.executemany(insert_query_resultados_salto, data_insert_resultados_salto)
conn.commit()

## Pruebas bbdd

In [7]:
pd.set_option('display.max_columns', None)

In [23]:
query1 = """
        SELECT * 
        FROM resultados r
            JOIN concursos c ON r.id_concurso = c.id_concurso
            JOIN pruebas p ON r.id_prueba = p.id_prueba;
"""
cur.execute(query1)
cosita = pd.DataFrame(cur.fetchall())
cosita.head()

0         1        2   3   4    5    6     7      8   9               10  \
0   1    284725   169882   1   1  1.0  FIN  True  450.0   1  CSN3* Invierno   
1   2     77612   157373   1   1  2.0  FIN  True  300.0   1  CSN3* Invierno   
2   3    306183   145996   1   1  3.0  FIN  True  200.0   1  CSN3* Invierno   
3   4  10006303  107ZP87   1   1  4.0  FIN  True  150.0   1  CSN3* Invierno   
4   5  10002400  105ZA09   1   1  5.0  FIN  True  125.0   1  CSN3* Invierno   

       11     12       13                14        15  \
0  CSN***  Epaña  Sevilla  Real Club Pineda  Nacional   
1  CSN***  Epaña  Sevilla  Real Club Pineda  Nacional   
2  CSN***  Epaña  Sevilla  Real Club Pineda  Nacional   
3  CSN***  Epaña  Sevilla  Real Club Pineda  Nacional   
4  CSN***  Epaña  Sevilla  Real Club Pineda  Nacional   

                           16          17          18  19  \
0  Federación Hípica Andaluza  2025-01-10  2025-01-12   1   
1  Federación Hípica Andaluza  2025-01-10  2025-01-12   1   
2  Federación Hípica Andaluza  2025-01-10  2025-01-12   1   
3  Federación Hípica Andaluza  2025-01-10  2025-01-12   1   
4  Federación Hípica Andaluza  2025-01-10  2025-01-12   1   

                        20          21  22  
0  1,30 - A c.c. (238.2.1)  2025-01-10   1  
1  1,30 - A c.c. (238.2.1)  2025-01-10   1  
2  1,30 - A c.c. (238.2.1)  2025-01-10   1  
3  1,30 - A c.c. (238.2.1)  2025-01-10   1  
4  1,30 - A c.c. (238.2.1)  2025-01-10   1

In [24]:
len(cosita[10].unique())

75

In [25]:
concursos_totales = []
concursos_malos = []
for _, elemento in cosita.iterrows():
    if elemento[17] <= elemento[21] <= elemento[18]:
        concursos_totales.append(elemento[10])
        print("ok")
    else:
        concursos_malos.append(elemento[10])
        print(elemento[10])

ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOUR

In [26]:
concursos_unicos_malos = list(set(concursos_malos))
concursos_unicos_malos

['SPRING MET II 2025 - SILVER 1*',
 'SPRING MET I 2025 - SILVER 1*',
 'SPRING MET I 2025 - BRONZE 1*',
 'SPRING MET I 2025 - YH*',
 'SPRING MET III 2025 - CSI3* GOLD',
 'SPRING MET I 2025 - GOLD 3*',
 'SPRING MET III 2025 - YH*',
 'SPRING MET III 2025 - CSI1* BRONZE',
 'RUTA GRANADA HIPICA',
 'SPRING MET II 2025 - BRONZE 1*',
 'SPRING MET II 2025 - GOLD 3*',
 'CSN2* RACE',
 'SPRING MET II 2025 - YH*',
 'CSN* C.H. DEL SUR - SEMANA SANTA',
 'SPRING MET IV - CSI1* BRONZE',
 'MOURA TOURS VALENCIA - SPRING TOUR',
 'CSN2* LAS CADENAS',
 'SPRING MET IV - YH*']

In [ ]:
query1 = """
        SELECT * 
        FROM resultados r
            JOIN concursos c ON r.id_concurso = c.id_concurso
            JOIN pruebas p ON r.id_prueba = p.id_prueba
            JOIN jinetes j ON r.id_jinete = j.id_jinete
            JOIN caballos c2 ON r.id_caballo = c2.id_caballo
            JOIN resultados_salto rs on r.id_resultado = rs.id_resultado;
"""
cur.execute(query1)
cosita = pd.DataFrame(cur.fetchall())
cosita.head()


0         1        2   3   4    5    6     7      8   9               10  \
0   1    284725   169882   1   1  1.0  FIN  True  450.0   1  CSN3* Invierno   
1   2     77612   157373   1   1  2.0  FIN  True  300.0   1  CSN3* Invierno   
2   3    306183   145996   1   1  3.0  FIN  True  200.0   1  CSN3* Invierno   
3   4  10006303  107ZP87   1   1  4.0  FIN  True  150.0   1  CSN3* Invierno   
4   5  10002400  105ZA09   1   1  5.0  FIN  True  125.0   1  CSN3* Invierno   

       11     12       13                14        15  \
0  CSN***  Epaña  Sevilla  Real Club Pineda  Nacional   
1  CSN***  Epaña  Sevilla  Real Club Pineda  Nacional   
2  CSN***  Epaña  Sevilla  Real Club Pineda  Nacional   
3  CSN***  Epaña  Sevilla  Real Club Pineda  Nacional   
4  CSN***  Epaña  Sevilla  Real Club Pineda  Nacional   

                           16          17          18  19  \
0  Federación Hípica Andaluza  2025-01-10  2025-01-12   1   
1  Federación Hípica Andaluza  2025-01-10  2025-01-12   1   
2  Federación Hípica Andaluza  2025-01-10  2025-01-12   1   
3  Federación Hípica Andaluza  2025-01-10  2025-01-12   1   
4  Federación Hípica Andaluza  2025-01-10  2025-01-12   1   

                        20          21  22        23  \
0  1,30 - A c.c. (238.2.1)  2025-01-10   1    284725   
1  1,30 - A c.c. (238.2.1)  2025-01-10   1     77612   
2  1,30 - A c.c. (238.2.1)  2025-01-10   1    306183   
3  1,30 - A c.c. (238.2.1)  2025-01-10   1  10006303   
4  1,30 - A c.c. (238.2.1)  2025-01-10   1  10002400   

                            24       25                   26  27  28   29  30  \
0  pedro miguel da silva manso   169882  bridgetown jones os   1   1  0.0 NaN   
1        ignacio astolfi lópez   157373       quinto blue ps   2   1  0.0 NaN   
2     francisco picao caldeira   145996         flor du paso   3   1  0.0 NaN   
3          jesús torres garcía  107ZP87          diabetto ps   4   1  0.0 NaN   
4              nina fagerstrom  105ZA09    hasenacher cervin   5   1  0.0 NaN   

      31  32  33  34  35    36  37  
0  59.91 NaN NaN NaN NaN  None NaN  
1  63.23 NaN NaN NaN NaN  None NaN  
2  65.58 NaN NaN NaN NaN  None NaN  
3  66.00 NaN NaN NaN NaN  None NaN  
4  66.78 NaN NaN NaN NaN  None NaN

In [19]:
len(cosita[10].unique())

75

In [20]:
concursos_totales = []
concursos_malos = []
for _, elemento in cosita.iterrows():
    if elemento[17] <= elemento[21] <= elemento[18]:
        concursos_totales.append(elemento[10])
        print("ok")
    else:
        concursos_malos.append(elemento[10])
        print(elemento[10])

ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOURS VALENCIA - SPRING TOUR
MOURA TOUR

In [16]:
concursos_unicos_totales = list(set(concursos_totales))
len(concursos_unicos_totales)

75

In [22]:
concursos_unicos_malos = list(set(concursos_malos))
concursos_unicos_malos

['SPRING MET II 2025 - SILVER 1*',
 'SPRING MET I 2025 - SILVER 1*',
 'SPRING MET I 2025 - BRONZE 1*',
 'SPRING MET I 2025 - YH*',
 'SPRING MET III 2025 - CSI3* GOLD',
 'SPRING MET I 2025 - GOLD 3*',
 'SPRING MET III 2025 - YH*',
 'SPRING MET III 2025 - CSI1* BRONZE',
 'RUTA GRANADA HIPICA',
 'SPRING MET II 2025 - BRONZE 1*',
 'SPRING MET II 2025 - GOLD 3*',
 'CSN2* RACE',
 'SPRING MET II 2025 - YH*',
 'CSN* C.H. DEL SUR - SEMANA SANTA',
 'SPRING MET IV - CSI1* BRONZE',
 'MOURA TOURS VALENCIA - SPRING TOUR',
 'CSN2* LAS CADENAS',
 'SPRING MET IV - YH*']

In [100]:
conn.rollback()

In [81]:
query1 = """
        SELECT * 
        FROM resultados r
            JOIN concursos c ON r.id_concurso = c.id_concurso
            JOIN pruebas p ON r.id_prueba = p.id_prueba
            JOIN jinetes j ON r.id_jinete = j.id_jinete
            JOIN caballos c2 ON r.id_caballo = c2.id_caballo;
"""
cur.execute(query1)
cosita = pd.DataFrame(cur.fetchall())
cosita.head()


0         1        2   3   4    5    6     7      8   9               10  \
0   1    284725   169882   1   1  1.0  FIN  True  450.0   1  CSN3* Invierno   
1   2     77612   157373   1   1  2.0  FIN  True  300.0   1  CSN3* Invierno   
2   3    306183   145996   1   1  3.0  FIN  True  200.0   1  CSN3* Invierno   
3   4  10006303  107ZP87   1   1  4.0  FIN  True  150.0   1  CSN3* Invierno   
4   5  10002400  105ZA09   1   1  5.0  FIN  True  125.0   1  CSN3* Invierno   

       11     12       13                14        15  \
0  CSN***  Epaña  Sevilla  Real Club Pineda  Nacional   
1  CSN***  Epaña  Sevilla  Real Club Pineda  Nacional   
2  CSN***  Epaña  Sevilla  Real Club Pineda  Nacional   
3  CSN***  Epaña  Sevilla  Real Club Pineda  Nacional   
4  CSN***  Epaña  Sevilla  Real Club Pineda  Nacional   

                           16          17          18  19  \
0  Federación Hípica Andaluza  2025-01-10  2025-01-12   1   
1  Federación Hípica Andaluza  2025-01-10  2025-01-12   1   
2  Federación Hípica Andaluza  2025-01-10  2025-01-12   1   
3  Federación Hípica Andaluza  2025-01-10  2025-01-12   1   
4  Federación Hípica Andaluza  2025-01-10  2025-01-12   1   

                        20          21  22        23  \
0  1,30 - A c.c. (238.2.1)  2025-01-10   1    284725   
1  1,30 - A c.c. (238.2.1)  2025-01-10   1     77612   
2  1,30 - A c.c. (238.2.1)  2025-01-10   1    306183   
3  1,30 - A c.c. (238.2.1)  2025-01-10   1  10006303   
4  1,30 - A c.c. (238.2.1)  2025-01-10   1  10002400   

                            24       25                   26  
0  pedro miguel da silva manso   169882  bridgetown jones os  
1        ignacio astolfi lópez   157373       quinto blue ps  
2     francisco picao caldeira   145996         flor du paso  
3          jesús torres garcía  107ZP87          diabetto ps  
4              nina fagerstrom  105ZA09    hasenacher cervin

In [41]:
len(cosita[25].unique())

KeyError: 25

In [89]:
df.columns

Index(['Estado', 'Posicion', 'Lic_jinete', 'Jinete', 'Lic_caballo', 'Caballo',
       'Premio', 'Dinero_premio', 'Prueba', 'Fecha_prueba', 'Concurso',
       'Categoria', 'Ptos_obs_R1', 'Ptos_tiempo_R1', 'Tiempo_R1',
       'Ptos_obs_R2', 'Ptos_tiempo_R2', 'Tiempo_R2', 'Ptos_obs_R3',
       'Ptos_tiempo_R3', 'Tiempo_R3', 'Provincia', 'Localidad', 'Disciplina',
       'Federación', 'País', 'Inicio', 'Final', 'Ambito', 'id_resultado'],
      dtype='object')

In [90]:
len(df["Lic_caballo"].unique())

8333

In [44]:
conn.rollback()

In [32]:
query1 = """
        SELECT DISTINCT
            r.id_resultado,
            p.nombre_prueba,
            p.fecha_prueba,
            c.fecha_inicio_concurso,
            c.fecha_fin_concurso
        FROM resultados r
            JOIN concursos c ON r.id_concurso = c.id_concurso
            JOIN pruebas p ON r.id_prueba = p.id_prueba
            JOIN jinetes j ON r.id_jinete = j.id_jinete
            JOIN caballos c2 ON r.id_caballo = c2.id_caballo
            JOIN resultados_salto rs on r.id_resultado = rs.id_resultado
        WHERE c.nombre_concurso = 'SPRING MET III 2025 - CSI3* GOLD';
"""
cur.execute(query1)
cosita = pd.DataFrame(cur.fetchall())
cosita

0                                         1           2           3  \
0     60220          1,40 (G) - Dos Fases (274.1.5.3)  2025-03-27  2025-03-27   
1     60392               1,40 (G) - A c.c. (238.2.1)  2025-03-28  2025-03-27   
2     55324              1,30 - Dos Fases (274.1.5.3)  2025-03-20  2025-03-27   
3     60379               1,40 (G) - A c.c. (238.2.1)  2025-03-28  2025-03-27   
4     60721  1,50 (GP) - A.c.c. y desempate (238.2.2)  2025-03-30  2025-03-27   
...     ...                                       ...         ...         ...   
1384  60653          1,45 (G) - Dos Fases (274.1.5.3)  2025-03-30  2025-03-27   
1385  60159                   1,30 - A c.c. (238.2.1)  2025-03-27  2025-03-27   
1386  55389               1,40 (G) - A c.c. (238.2.1)  2025-03-20  2025-03-27   
1387  55971          1,45 (G) - Dos Fases (274.1.5.3)  2025-03-23  2025-03-27   
1388  55849   1,45 (G) - A.c.c. y desempate (238.2.2)  2025-03-22  2025-03-27   

               4  
0     2025-03-30  
1     2025-03-30  
2     2025-03-30  
3     2025-03-30  
4     2025-03-30  
...          ...  
1384  2025-03-30  
1385  2025-03-30  
1386  2025-03-30  
1387  2025-03-30  
1388  2025-03-30  

[1389 rows x 5 columns]

In [6]:
import pandas as pd

In [33]:
query1 = """
        SELECT *
        FROM concursos c
        WHERE c.nombre_concurso = 'SPRING MET III 2025 - CSI3* GOLD';
"""
cur.execute(query1)
cosita = pd.DataFrame(cur.fetchall())
cosita

0                                 1       2      3         4  \
0  87  SPRING MET III 2025 - CSI3* GOLD  CSI***  Epaña  Valencia   
1  96  SPRING MET III 2025 - CSI3* GOLD  CSI***  Epaña  Valencia   

                            5              6  \
0  Centro Ecuestre Oliva Nova  Internacional   
1  Centro Ecuestre Oliva Nova  Internacional   

                                        7           8           9  
0  Federación Hípica Comunidad Valenciana  2025-03-20  2025-03-23  
1  Federación Hípica Comunidad Valenciana  2025-03-27  2025-03-30

In [30]:
pd.set_option('display.max_columns', None)


In [35]:
query1 = """
        SELECT *
        FROM resultados r
            JOIN concursos c ON r.id_concurso = c.id_concurso
            JOIN pruebas p ON r.id_prueba = p.id_prueba
        WHERE c.nombre_concurso = 'SPRING MET III 2025 - CSI3* GOLD' AND c.fecha_inicio_concurso = DATE '2025-03-27';
"""
cur.execute(query1)
cosita = pd.DataFrame(cur.fetchall())
cosita

0         1        2    3   4     5    6     7      8   9   \
0     55319  10147980  108OJ53  823  96   1.0  FIN  True  250.0  96   
1     55320  10019052  107BW27  823  96   2.0  FIN  True  200.0  96   
2     55321  10106266  109AO27  823  96   3.0  FIN  True  150.0  96   
3     55322  10008039  106TN09  823  96   4.0  FIN  True  100.0  96   
4     55323  10009752  108QW50  823  96   5.0  FIN  True   70.0  96   
...     ...       ...      ...  ...  ..   ...  ...   ...    ...  ..   
1384  60766  10041027  107DG94  932  96  47.0  FIN  True    0.0  96   
1385  60767  10023889  105YI36  932  96  48.0  FIN  True    0.0  96   
1386  60768  10025845  107KL32  932  96  49.0  FIN  True    0.0  96   
1387  60769  10040081  107PP25  932  96   NaN  RET  True    0.0  96   
1388  60770  10089313  107AA38  932  96   NaN  RET  True    0.0  96   

                                    10      11     12        13  \
0     SPRING MET III 2025 - CSI3* GOLD  CSI***  Epaña  Valencia   
1     SPRING MET III 2025 - CSI3* GOLD  CSI***  Epaña  Valencia   
2     SPRING MET III 2025 - CSI3* GOLD  CSI***  Epaña  Valencia   
3     SPRING MET III 2025 - CSI3* GOLD  CSI***  Epaña  Valencia   
4     SPRING MET III 2025 - CSI3* GOLD  CSI***  Epaña  Valencia   
...                                ...     ...    ...       ...   
1384  SPRING MET III 2025 - CSI3* GOLD  CSI***  Epaña  Valencia   
1385  SPRING MET III 2025 - CSI3* GOLD  CSI***  Epaña  Valencia   
1386  SPRING MET III 2025 - CSI3* GOLD  CSI***  Epaña  Valencia   
1387  SPRING MET III 2025 - CSI3* GOLD  CSI***  Epaña  Valencia   
1388  SPRING MET III 2025 - CSI3* GOLD  CSI***  Epaña  Valencia   

                              14             15  \
0     Centro Ecuestre Oliva Nova  Internacional   
1     Centro Ecuestre Oliva Nova  Internacional   
2     Centro Ecuestre Oliva Nova  Internacional   
3     Centro Ecuestre Oliva Nova  Internacional   
4     Centro Ecuestre Oliva Nova  Internacional   
...                          ...            ...   
1384  Centro Ecuestre Oliva Nova  Internacional   
1385  Centro Ecuestre Oliva Nova  Internacional   
1386  Centro Ecuestre Oliva Nova  Internacional   
1387  Centro Ecuestre Oliva Nova  Internacional   
1388  Centro Ecuestre Oliva Nova  Internacional   

                                          16          17          18   19  \
0     Federación Hípica Comunidad Valenciana  2025-03-27  2025-03-30  823   
1     Federación Hípica Comunidad Valenciana  2025-03-27  2025-03-30  823   
2     Federación Hípica Comunidad Valenciana  2025-03-27  2025-03-30  823   
3     Federación Hípica Comunidad Valenciana  2025-03-27  2025-03-30  823   
4     Federación Hípica Comunidad Valenciana  2025-03-27  2025-03-30  823   
...                                      ...         ...         ...  ...   
1384  Federación Hípica Comunidad Valenciana  2025-03-27  2025-03-30  932   
1385  Federación Hípica Comunidad Valenciana  2025-03-27  2025-03-30  932   
1386  Federación Hípica Comunidad Valenciana  2025-03-27  2025-03-30  932   
1387  Federación Hípica Comunidad Valenciana  2025-03-27  2025-03-30  932   
1388  Federación Hípica Comunidad Valenciana  2025-03-27  2025-03-30  932   

                                            20          21  22  
0                 1,30 - Dos Fases (274.1.5.3)  2025-03-20   1  
1                 1,30 - Dos Fases (274.1.5.3)  2025-03-20   1  
2                 1,30 - Dos Fases (274.1.5.3)  2025-03-20   1  
3                 1,30 - Dos Fases (274.1.5.3)  2025-03-20   1  
4                 1,30 - Dos Fases (274.1.5.3)  2025-03-20   1  
...                                        ...         ...  ..  
1384  1,50 (GP) - A.c.c. y desempate (238.2.2)  2025-03-30   1  
1385  1,50 (GP) - A.c.c. y desempate (238.2.2)  2025-03-30   1  
1386  1,50 (GP) - A.c.c. y desempate (238.2.2)  2025-03-30   1  
1387  1,50 (GP) - A.c.c. y desempate (238.2.2)  2025-03-30   1  
1388  1,50 (GP) - A.c.c. y desempate (238.2.2)  2025-03-30   1  

[1389 rows x 23 columns]

In [36]:
df[df["Concurso"] == "SPRING MET III 2025 - CSI3* GOLD"]

Estado Posicion  Lic_jinete                  Jinete Lic_caballo  \
169280    FIN        1    10147980      christopher franks     108OJ53   
169282    FIN        2    10019052      ricardo gil santos     107BW27   
169284    FIN        3    10106266          axel vandoorne     109AO27   
169286    FIN        4    10008039           steven franks     106TN09   
169288    FIN        5    10009752         jenny johansson     108QW50   
...       ...      ...         ...                     ...         ...   
177708    FIN       47    10041027             alicia page     107DG94   
177710    FIN       48    10023889       isabell bengtsson     105YI36   
177712    FIN       49    10025845          maurice tebbel     107KL32   
177714    RET      NaN    10040081     kristaps neretnieks     107PP25   
177716    RET      NaN    10089313  benedikte rie truelsen     107AA38   

                        Caballo  Premio  Dinero_premio  \
169280   whitney vd berendskamp    True          250.0   
169282         first diamond ag    True          200.0   
169284  rosie van het wilderhof    True          150.0   
169286     invictus d'ayrifagne    True          100.0   
169288              viva verona    True           70.0   
...                         ...     ...            ...   
177708          fermoyle prince    True            0.0   
177710               il divo bs    True            0.0   
177712  crazy for you de tiji z    True            0.0   
177714            corlansky-pro    True            0.0   
177716                obahma js    True            0.0   

                                          Prueba Fecha_prueba  \
169280              1,30 - Dos Fases (274.1.5.3)   2025-03-20   
169282              1,30 - Dos Fases (274.1.5.3)   2025-03-20   
169284              1,30 - Dos Fases (274.1.5.3)   2025-03-20   
169286              1,30 - Dos Fases (274.1.5.3)   2025-03-20   
169288              1,30 - Dos Fases (274.1.5.3)   2025-03-20   
...                                          ...          ...   
177708  1,50 (GP) - A.c.c. y desempate (238.2.2)   2025-03-30   
177710  1,50 (GP) - A.c.c. y desempate (238.2.2)   2025-03-30   
177712  1,50 (GP) - A.c.c. y desempate (238.2.2)   2025-03-30   
177714  1,50 (GP) - A.c.c. y desempate (238.2.2)   2025-03-30   
177716  1,50 (GP) - A.c.c. y desempate (238.2.2)   2025-03-30   

                                Concurso Categoria  Ptos_obs_R1  \
169280  SPRING MET III 2025 - CSI3* GOLD    CSI***          0.0   
169282  SPRING MET III 2025 - CSI3* GOLD    CSI***          0.0   
169284  SPRING MET III 2025 - CSI3* GOLD    CSI***          0.0   
169286  SPRING MET III 2025 - CSI3* GOLD    CSI***          0.0   
169288  SPRING MET III 2025 - CSI3* GOLD    CSI***          0.0   
...                                  ...       ...          ...   
177708  SPRING MET III 2025 - CSI3* GOLD    CSI***          4.0   
177710  SPRING MET III 2025 - CSI3* GOLD    CSI***         16.0   
177712  SPRING MET III 2025 - CSI3* GOLD    CSI***          8.0   
177714  SPRING MET III 2025 - CSI3* GOLD    CSI***          NaN   
177716  SPRING MET III 2025 - CSI3* GOLD    CSI***          NaN   

        Ptos_tiempo_R1  Tiempo_R1  Ptos_obs_R2  Ptos_tiempo_R2  Tiempo_R2  \
169280             NaN      46.78          0.0             NaN      26.81   
169282             NaN      45.17          0.0             NaN      27.03   
169284             NaN      47.22          0.0             NaN      27.86   
169286             NaN      48.15          0.0             NaN      28.47   
169288             NaN      44.97          0.0             NaN      29.72   
...                ...        ...          ...             ...        ...   
177708            11.0      87.96          NaN             NaN        NaN   
177710             1.0      77.32          NaN             NaN        NaN   
177712            11.0      87.20          NaN             NaN        NaN   
177714             NaN        NaN          NaN             NaN   

In [37]:
coso = df_resultados[df_resultados["Concurso"] == "SPRING MET III 2025 - CSI3* GOLD"]
coso

id_resultado                  Jinete                  Caballo  \
169280         55319      christopher franks   whitney vd berendskamp   
169282         55320      ricardo gil santos         first diamond ag   
169284         55321          axel vandoorne  rosie van het wilderhof   
169286         55322           steven franks     invictus d'ayrifagne   
169288         55323         jenny johansson              viva verona   
...              ...                     ...                      ...   
177708         60766             alicia page          fermoyle prince   
177710         60767       isabell bengtsson               il divo bs   
177712         60768          maurice tebbel  crazy for you de tiji z   
177714         60769     kristaps neretnieks            corlansky-pro   
177716         60770  benedikte rie truelsen                obahma js   

                                Concurso  \
169280  SPRING MET III 2025 - CSI3* GOLD   
169282  SPRING MET III 2025 - CSI3* GOLD   
169284  SPRING MET III 2025 - CSI3* GOLD   
169286  SPRING MET III 2025 - CSI3* GOLD   
169288  SPRING MET III 2025 - CSI3* GOLD   
...                                  ...   
177708  SPRING MET III 2025 - CSI3* GOLD   
177710  SPRING MET III 2025 - CSI3* GOLD   
177712  SPRING MET III 2025 - CSI3* GOLD   
177714  SPRING MET III 2025 - CSI3* GOLD   
177716  SPRING MET III 2025 - CSI3* GOLD   

                                          Prueba Posicion Estado  Premio  \
169280              1,30 - Dos Fases (274.1.5.3)        1    FIN    True   
169282              1,30 - Dos Fases (274.1.5.3)        2    FIN    True   
169284              1,30 - Dos Fases (274.1.5.3)        3    FIN    True   
169286              1,30 - Dos Fases (274.1.5.3)        4    FIN    True   
169288              1,30 - Dos Fases (274.1.5.3)        5    FIN    True   
...                                          ...      ...    ...     ...   
177708  1,50 (GP) - A.c.c. y desempate (238.2.2)       47    FIN    True   
177710  1,50 (GP) - A.c.c. y desempate (238.2.2)       48    FIN    True   
177712  1,50 (GP) - A.c.c. y desempate (238.2.2)       49    FIN    True   
177714  1,50 (GP) - A.c.c. y desempate (238.2.2)      NaN    RET    True   
177716  1,50 (GP) - A.c.c. y desempate (238.2.2)      NaN    RET    True   

        Dinero_premio Fecha_prueba     Inicio      Final  
169280          250.0   2025-03-20 2025-03-20 2025-03-23  
169282          200.0   2025-03-20 2025-03-20 2025-03-23  
169284          150.0   2025-03-20 2025-03-20 2025-03-23  
169286          100.0   2025-03-20 2025-03-20 2025-03-23  
169288           70.0   2025-03-20 2025-03-20 2025-03-23  
...               ...          ...        ...        ...  
177708            0.0   2025-03-30 2025-03-27 2025-03-30  
177710            0.0   2025-03-30 2025-03-27 2025-03-30  
177712            0.0   2025-03-30 2025-03-27 2025-03-30  
177714            0.0   2025-03-30 2025-03-27 2025-03-30  
177716            0.0   2025-03-30 2025-03-27 2025-03-30  

[1389 rows x 12 columns]

In [38]:
concursos_totales = []
concursos_malos = []
for _, elemento in coso.iterrows():
    if elemento["Inicio"] <= elemento["Fecha_prueba"] <= elemento["Final"]:
        concursos_totales.append(elemento["Concurso"])
        print("ok")
    else:
        concursos_malos.append(elemento["Concurso"])
        print(elemento["Concurso"])

ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
ok
o